MIT License

Copyright (c) 2017 Ryan Whytsell

Permission is hereby granted, free of charge, to any person obtaining a copy
of this software and associated documentation files (the "Software"), to deal
in the Software without restriction, including without limitation the rights
to use, copy, modify, merge, publish, distribute, sublicense, and/or sell
copies of the Software, and to permit persons to whom the Software is
furnished to do so, subject to the following conditions:

The above copyright notice and this permission notice shall be included in all
copies or substantial portions of the Software.

THE SOFTWARE IS PROVIDED "AS IS", WITHOUT WARRANTY OF ANY KIND, EXPRESS OR
IMPLIED, INCLUDING BUT NOT LIMITED TO THE WARRANTIES OF MERCHANTABILITY,
FITNESS FOR A PARTICULAR PURPOSE AND NONINFRINGEMENT. IN NO EVENT SHALL THE
AUTHORS OR COPYRIGHT HOLDERS BE LIABLE FOR ANY CLAIM, DAMAGES OR OTHER
LIABILITY, WHETHER IN AN ACTION OF CONTRACT, TORT OR OTHERWISE, ARISING FROM,
OUT OF OR IN CONNECTION WITH THE SOFTWARE OR THE USE OR OTHER DEALINGS IN THE
SOFTWARE.


Modified by Harish Iyer Ganesan

In [1]:
import sys
import pygame
import random
from threading import Thread
#import PreyPredator
import time

import warnings
warnings.filterwarnings("ignore")

pygame 2.1.0 (SDL 2.0.16, Python 3.8.3)
Hello from the pygame community. https://www.pygame.org/contribute.html


In [2]:
import random
import sys
import copy
random.seed(1)

In [3]:
import csv


In [4]:
class Node:

    species = None
    x = None
    y = None
    health = None
    

    def __init__(self, spec=None):
        if spec is not None:
            self.species = spec
        else:
            self.species = 0
        self.x = None
        self.y = None
        #self.health = self.species*2
        if spec is 0:  # Blank
            self.health = None
        if spec is 1:  # Predator
            self.health = 2
        if spec is 2:  #Intermediate-Predator
            self.health = 3
        if spec is 3:  # Prey
            self.health = 4

    def set_location(self, pos_x, pos_y):
        self.x = pos_x
        self.y = pos_y

    def set_species(self, num):
        if num == 0 or num == 1 or num == 2 or num == 3:
            self.species = num
            if num is 0:  # Blank
                self.health = None
            if num is 1:  # Predator
                self.health = 2
            if num is 2:  #Intermediate-Predator
                self.health = 2
            if num is 3:  # Prey
                self.health = 4
        else:
            sys.stderr.write('Species not correct, do not do math with them.')
            self.species = 0

    def move_here(self, species, health):
        if species == 0 or species == 1 or species == 2 or species == 3:
            self.species = species
            if species is 0:  # Blank
                self.health = health
            if species is 1:  # Predator
                self.health = health
            if species is 2:  #Intermediate-Predator
                self.health = health
            if species is 3:  # Prey
                self.health = health
        else:
            sys.stderr.write('Species not correct, do not do math with them.')
            self.species = 0

    def prey_eat(self):
        self.species = 1
        #self.health = 2
            
    def predator_eat_intermediate_predator(self):
        self.species = 1
        #self.health = 2
            
    def intermediate_predator_prey_eat(self):
        self.species = 2
        #self.health = 3

            
    def intermediate_predator_reproduce(self):
        self.species = 2
        #self.health = 3

    def prey_reproduce(self):
        self.species = 3
        self.health = 4

In [5]:
class Map:
    height = 100
    width = 100
    play_board = []
    kill_count = 0
    prey_kill_count = 0
    
    def __init__(self):
        
        prey = 0
        predator = 0
        intermediate_predator = 0
        empty = 0       
        for x in range(self.width):
            row = []
            
#             # Random Spatial Dostribution
#             for y in range(self.height):
#                 i = random.randint(0, 100)
#                 if i <= 25:
#                     row.append(Node(3))
#                     prey += 1
#                 elif i <= 50 :
#                     row.append(Node(2))
#                     intermediate_predator += 1
#                 elif i<= 75:
#                     row.append(Node(1))
#                     predator += 1
#                 else:
#                     row.append(Node(0))
#                     empty += 1
               
            #Clustered Spatial Dostribution
            for y in range(self.height):
                i = random.randint(0, 100)
                if i <= 25 and x<50 and y<50:
                    row.append(Node(3))
                    prey += 1
                elif i <= 25 and x>50 and y>50:
                    row.append(Node(3))
                    prey += 1
                elif i <= 50 and x<50 and y<50:
                    row.append(Node(2))
                    intermediate_predator += 1
                elif i <= 75 and x>50 and y>50:
                    row.append(Node(1))
                    predator += 1
                else:
                    row.append(Node(0))
                    empty += 1

            self.play_board.append(row)
        print('Map created')
        print('Prey: ', prey)
        print('Intermediate-Predator: ', intermediate_predator)
        print('Predator: ', predator)
        print('Empty: ', empty)
        print('Width: ', len(self.play_board))
        print('Height of row 5: ', len(self.play_board[5]))
        #writer.writerow({'time_step': 0, 'prey': prey, 'intermediate_predator': intermediate_predator, 'predator': predator, 'empty': empty  })
    
    def map_count(self, time_step,writer):
        pb = self.play_board
        prey = 0
        predator = 0
        intermediate_predator = 0
        empty = 0
        for x in range(0, self.width):
            for y in range(0, self.height):
                if  pb[x][y].species is 3:
                    prey += 1
                elif pb[x][y].species is 2:
                    intermediate_predator += 1
                elif pb[x][y].species is 1:
                    predator += 1
                else:
                    empty += 1
                
                
        print('Time Step: ',time_step)
        print('Prey: ', prey)
        print('Intermediate-Predator: ', intermediate_predator)
        print('Predator: ', predator)
        print('Empty: ', empty)
        print('-----------------------------------------')
        writer.writerow({'time_step': time_step, 'prey': prey, 'intermediate_predator': intermediate_predator, 'predator': predator, 'empty': empty  })

    
    def get_board(self):
        return self.play_board

    def turn(self):
        pb = self.play_board
        [[self.check_neighbors(x, y, pb[x][y]) for y in range(0, self.height)] for x in range(0, self.width)]

    # Returns the neighbors of a node, If node is on edge this wraps
    def get_neighbors(self, x, y):
        top = self.play_board[x][(y - 1) % self.height]
        tr = self.play_board[(x + 1) % self.width][(y - 1) % self.height]
        right = self.play_board[(x + 1) % self.width][y]
        br = self.play_board[(x + 1) % self.width][(y + 1) % self.height]
        bottom = self.play_board[x][(y + 1) % self.height]
        bl = self.play_board[(x - 1) % self.width][(y + 1) % self.height]
        left = self.play_board[(x - 1) % self.width][y]
        tl = self.play_board[(x - 1) % self.width][(y - 1) % self.height]

        neighbors = [top, tr, right, br, bottom, bl, left, tl]
        #neighbors = [top, right, bottom, left]
        return neighbors

    #
    # PREDATOR AND PREY CELLULAR AUTOMATON
    # The world is grid of cells, with 4 possibilities: Predator(Red, 1), Intermediate-Predator(Yellow, 2) Prey(Blue, 3), or Empty(Black, 0).
    # All predator, intermediate-predator and prey have a set health, that changes over time.
    # The simulation works in steps, with the following rules:
    #    -For prey:
    #        -Tries to move in a random direction.
    #        -Health increases.
    #        -When health reaches a threshold:
    #           -They will reproduce, creating a new "Prey"
    #            -Their health resets to 1
    #    -For intermediate-predator:
    #        -Tries to move in a random direction.
    #        -Health decreases.
    #        -When health reaches 0, they die and turn into "Nothing".
    #       -If the adjacent square is a prey:
    #            -They will eat it, turning it into a "predator" (reproducing)
    #            -Their health will increase by the amount of health the eaten prey had
    #    -For predator:
    #        -Tries to move in a random direction.
    #        -Health decreases.
    #        -When health reaches 0, they die and turn into "Nothing".
    #       -If the adjacent square is a prey:
    #            -They will eat it, turning it into a "predator" (reproducing)     
    #            -Their health will increase by the amount of health the eaten prey had
    
    def check_neighbors(self, x, y, node):
        # If the node is empty no checks are performed
        if node.species is 0:
            return

        if node.species is 1:
            # This is a predator. Check for prey if no prey reduce health/die
            neighbors = self.get_neighbors(x, y)
            prey = []
            intermediate_predator = []
            open_ = []

            for neigh in neighbors:
                if neigh.species is 3:
                    prey.append(neigh)
                if neigh.species is 2:
                    intermediate_predator.append(neigh)
                if neigh.species is 0:
                    open_.append(neigh)
            open_length = len(open_)

            
            if len(prey) is 0 and len(intermediate_predator) is 0:
                if node.health > 0 and open_length > 0:
                    node.health -= 1
                    open_[random.randint(0, (open_length-1))].move_here(1, node.health)
                    node.set_species(0)
                else:
                    node.health -= 1
                                
            elif len(prey) > 0:
                target = prey[random.randint(0, (len(prey)-1))]
                if node.health >= target.health:
                    target.prey_eat() 
                    self.prey_kill_count+=1
                elif len(intermediate_predator)>0:
                    target = intermediate_predator[random.randint(0, (len(intermediate_predator)-1))]
                    if node.health >= target.health:
                        target.predator_eat_intermediate_predator()
                        self.kill_count+=1
                        
            elif len(intermediate_predator)>0:
                target = intermediate_predator[random.randint(0, (len(intermediate_predator)-1))]
                if node.health >= target.health:
                    target.predator_eat_intermediate_predator()
                else:
                    node.health -= 1
                          
            if node.health is None or node.health <= 0:
                node.set_species(0)
                return

        if node.species is 2:
            # This is an intermediate-predator. Check for prey if no prey reduce health/die
            neighbors = self.get_neighbors(x, y)
            prey = []
            predator = []
            open_ = []

            for neigh in neighbors:
                if neigh.species is 3:
                    prey.append(neigh)
                if neigh.species is 1:
                    predator.append(neigh)
                if neigh.species is 0:
                    open_.append(neigh)
            open_length = len(open_)
            

            if len(prey) is 0:
                if node.health >0  and open_length > 0:
                    node.health -= 1
                    open_[random.randint(0, (open_length-1))].move_here(2, node.health)
                    node.set_species(0)
                else:
                    node.health -= 1
            else:
                target = prey[random.randint(0, (len(prey)-1))]
                if node.health >= target.health:
                    target.intermediate_predator_prey_eat()
                    self.prey_kill_count+=1

            if node.health is None or node.health <= 0:
                node.set_species(0)
                return
            
#             if node.health > 4 and open_length >= 1:
#                 open_[random.randint(0, (open_length-1))].intermediate_predator_reproduce()
#                 node.health = 2
#                 return            
            
        if node.species is 3:
            # Check for overpopulation/health This is prey
            neighbors = self.get_neighbors(x, y)
            open_spots = []
            for neigh in neighbors:
                if neigh.species is 0:
                    open_spots.append(neigh)
            count = len(open_spots)
            if count >= 7 or count < 1:
                node.health -= 2
            if node.health is None or node.health is 0:
                node.set_species(0)
                return
            if node.health > 6 and len(open_spots) >= 1:
                open_spots[random.randint(0, (len(open_spots))-1)].prey_reproduce()
                node.health = 4
                return
            node.health += 1

In [6]:
#random.seed(1)
size = width, height = 500, 500
play_width = width/5
play_height = height/5
is_stopped = False

In [7]:
# These are the codes that pygame uses, I am not sure what format it is
black = 0
red = ((255,0,0))
yellow = ((255,255,0))
blue = ((0,0,255))

color_arr = [black, red, yellow, blue]

In [8]:
pygame.init()
screen = pygame.display.set_mode(size)
pp = Map()

Map created
Prey:  1252
Intermediate-Predator:  628
Predator:  1183
Empty:  6937
Width:  100
Height of row 5:  100


In [9]:
# Paints a 3x3 square for each node
def paint(x, y, color_int):
    screen.set_at((x, y), color_arr[color_int])
    screen.set_at((x + 1, y), color_arr[color_int])
    screen.set_at((x, y + 1), color_arr[color_int])
    screen.set_at((x + 1, y + 1), color_arr[color_int])
    screen.set_at((x + 2, y), color_arr[color_int])
    screen.set_at((x, y + 2), color_arr[color_int])
    screen.set_at((x + 2, y + 2), color_arr[color_int])
    screen.set_at((x + 2, y + 1), color_arr[color_int])
    screen.set_at((x + 1, y + 2), color_arr[color_int])

In [10]:
# Creates random colors TESTING ONLY
def random_colors(w, h):
    ra = random.randint
    pa = paint
    while not is_stopped:
        for x in range(5, w, 5):
            for y in range(5, h, 5):
                color_int = ra(1, 2)
                pa(x, y, color_int)

In [11]:
# Paints the species at each point on the play board
def paint_map(board):
    pa = paint
    length = len(board)
    for x in range(0, length):
        for y in range(0, length):
            pa(x*5, y*5, board[x][y].species)

In [12]:
#### Game loop, paints the map then calculates the next turn
time_step=0
#open the file in the write mode
with open('1prey_2predator_Asymmetric.csv', 'w', newline='') as csvfile:
    fieldnames = ['time_step', 'prey','intermediate_predator','predator','empty']
    writer = csv.DictWriter(csvfile, fieldnames=fieldnames)
    writer.writeheader()
    while True:
        for event in pygame.event.get():
            if event.type == pygame.QUIT:
                is_stopped = True
                sys.exit(0)
        paint_map(pp.get_board())
        pygame.display.flip()
        pp.map_count(time_step, writer)
        pp.turn()
#         if(time_step==0 or time_step==200 or time_step==500 or time_step==1000):
#             a=input("Stop for snapshot")
        if(time_step==0 or time_step==500):
            time.sleep(10)
            print("Kill Count: ", pp.kill_count)
            print("Prey Kill Count: ",pp.prey_kill_count)
            pygame.QUIT
            #a=input("Stop for snapshot")
        time_step+=1
            

Time Step:  0
Prey:  1252
Intermediate-Predator:  628
Predator:  1183
Empty:  6937
-----------------------------------------
Kill Count:  0
Prey Kill Count:  4
Time Step:  1
Prey:  1248
Intermediate-Predator:  629
Predator:  1181
Empty:  6942
-----------------------------------------
Time Step:  2
Prey:  1206
Intermediate-Predator:  621
Predator:  1179
Empty:  6994
-----------------------------------------
Time Step:  3
Prey:  1181
Intermediate-Predator:  604
Predator:  1153
Empty:  7062
-----------------------------------------
Time Step:  4
Prey:  2186
Intermediate-Predator:  604
Predator:  1142
Empty:  6068
-----------------------------------------
Time Step:  5
Prey:  2102
Intermediate-Predator:  648
Predator:  1168
Empty:  6082
-----------------------------------------
Time Step:  6
Prey:  1811
Intermediate-Predator:  740
Predator:  1326
Empty:  6123
-----------------------------------------
Time Step:  7
Prey:  1897
Intermediate-Predator:  799
Predator:  1468
Empty:  5836
-------

Time Step:  66
Prey:  2884
Intermediate-Predator:  648
Predator:  1214
Empty:  5254
-----------------------------------------
Time Step:  67
Prey:  2888
Intermediate-Predator:  664
Predator:  1223
Empty:  5225
-----------------------------------------
Time Step:  68
Prey:  2855
Intermediate-Predator:  696
Predator:  1248
Empty:  5201
-----------------------------------------
Time Step:  69
Prey:  2819
Intermediate-Predator:  731
Predator:  1254
Empty:  5196
-----------------------------------------
Time Step:  70
Prey:  2825
Intermediate-Predator:  752
Predator:  1271
Empty:  5152
-----------------------------------------
Time Step:  71
Prey:  2811
Intermediate-Predator:  793
Predator:  1324
Empty:  5072
-----------------------------------------
Time Step:  72
Prey:  2817
Intermediate-Predator:  809
Predator:  1354
Empty:  5020
-----------------------------------------
Time Step:  73
Prey:  2786
Intermediate-Predator:  838
Predator:  1360
Empty:  5016
----------------------------------

Time Step:  132
Prey:  2735
Intermediate-Predator:  1061
Predator:  1642
Empty:  4562
-----------------------------------------
Time Step:  133
Prey:  2716
Intermediate-Predator:  1055
Predator:  1609
Empty:  4620
-----------------------------------------
Time Step:  134
Prey:  2692
Intermediate-Predator:  1069
Predator:  1597
Empty:  4642
-----------------------------------------
Time Step:  135
Prey:  2673
Intermediate-Predator:  1051
Predator:  1601
Empty:  4675
-----------------------------------------
Time Step:  136
Prey:  2681
Intermediate-Predator:  1029
Predator:  1630
Empty:  4660
-----------------------------------------
Time Step:  137
Prey:  2628
Intermediate-Predator:  1035
Predator:  1647
Empty:  4690
-----------------------------------------
Time Step:  138
Prey:  2583
Intermediate-Predator:  1062
Predator:  1659
Empty:  4696
-----------------------------------------
Time Step:  139
Prey:  2587
Intermediate-Predator:  1087
Predator:  1665
Empty:  4661
------------------

Time Step:  197
Prey:  2548
Intermediate-Predator:  1132
Predator:  1493
Empty:  4827
-----------------------------------------
Time Step:  198
Prey:  2529
Intermediate-Predator:  1109
Predator:  1500
Empty:  4862
-----------------------------------------
Time Step:  199
Prey:  2541
Intermediate-Predator:  1046
Predator:  1516
Empty:  4897
-----------------------------------------
Time Step:  200
Prey:  2548
Intermediate-Predator:  1020
Predator:  1531
Empty:  4901
-----------------------------------------
Time Step:  201
Prey:  2543
Intermediate-Predator:  1013
Predator:  1505
Empty:  4939
-----------------------------------------
Time Step:  202
Prey:  2530
Intermediate-Predator:  1003
Predator:  1452
Empty:  5015
-----------------------------------------
Time Step:  203
Prey:  2565
Intermediate-Predator:  994
Predator:  1408
Empty:  5033
-----------------------------------------
Time Step:  204
Prey:  2594
Intermediate-Predator:  993
Predator:  1401
Empty:  5012
--------------------

Time Step:  263
Prey:  2861
Intermediate-Predator:  1241
Predator:  1150
Empty:  4748
-----------------------------------------
Time Step:  264
Prey:  2926
Intermediate-Predator:  1256
Predator:  1137
Empty:  4681
-----------------------------------------
Time Step:  265
Prey:  2980
Intermediate-Predator:  1285
Predator:  1145
Empty:  4590
-----------------------------------------
Time Step:  266
Prey:  2965
Intermediate-Predator:  1337
Predator:  1156
Empty:  4542
-----------------------------------------
Time Step:  267
Prey:  2917
Intermediate-Predator:  1385
Predator:  1159
Empty:  4539
-----------------------------------------
Time Step:  268
Prey:  2961
Intermediate-Predator:  1402
Predator:  1122
Empty:  4515
-----------------------------------------
Time Step:  269
Prey:  2964
Intermediate-Predator:  1425
Predator:  1144
Empty:  4467
-----------------------------------------
Time Step:  270
Prey:  2958
Intermediate-Predator:  1433
Predator:  1144
Empty:  4465
------------------

...

Time Step:  23930
Prey:  2560
Intermediate-Predator:  1310
Predator:  1167
Empty:  4963
-----------------------------------------
Time Step:  23931
Prey:  2538
Intermediate-Predator:  1308
Predator:  1175
Empty:  4979
-----------------------------------------
Time Step:  23932
Prey:  2539
Intermediate-Predator:  1330
Predator:  1184
Empty:  4947
-----------------------------------------
Time Step:  23933
Prey:  2541
Intermediate-Predator:  1305
Predator:  1185
Empty:  4969
-----------------------------------------
Time Step:  23934
Prey:  2529
Intermediate-Predator:  1293
Predator:  1185
Empty:  4993
-----------------------------------------
Time Step:  23935
Prey:  2520
Intermediate-Predator:  1289
Predator:  1195
Empty:  4996
-----------------------------------------
Time Step:  23936
Prey:  2503
Intermediate-Predator:  1305
Predator:  1187
Empty:  5005
-----------------------------------------
Time Step:  23937
Prey:  2534
Intermediate-Predator:  1269
Predator:  1164
Empty:  5033
--

Time Step:  23996
Prey:  2499
Intermediate-Predator:  1159
Predator:  1238
Empty:  5104
-----------------------------------------
Time Step:  23997
Prey:  2547
Intermediate-Predator:  1158
Predator:  1211
Empty:  5084
-----------------------------------------
Time Step:  23998
Prey:  2585
Intermediate-Predator:  1132
Predator:  1228
Empty:  5055
-----------------------------------------
Time Step:  23999
Prey:  2598
Intermediate-Predator:  1138
Predator:  1234
Empty:  5030
-----------------------------------------
Time Step:  24000
Prey:  2654
Intermediate-Predator:  1134
Predator:  1244
Empty:  4968
-----------------------------------------
Time Step:  24001
Prey:  2658
Intermediate-Predator:  1146
Predator:  1252
Empty:  4944
-----------------------------------------
Time Step:  24002
Prey:  2646
Intermediate-Predator:  1153
Predator:  1264
Empty:  4937
-----------------------------------------
Time Step:  24003
Prey:  2649
Intermediate-Predator:  1145
Predator:  1277
Empty:  4929
--

Time Step:  24060
Prey:  2644
Intermediate-Predator:  1303
Predator:  1151
Empty:  4902
-----------------------------------------
Time Step:  24061
Prey:  2642
Intermediate-Predator:  1296
Predator:  1105
Empty:  4957
-----------------------------------------
Time Step:  24062
Prey:  2678
Intermediate-Predator:  1283
Predator:  1096
Empty:  4943
-----------------------------------------
Time Step:  24063
Prey:  2679
Intermediate-Predator:  1272
Predator:  1104
Empty:  4945
-----------------------------------------
Time Step:  24064
Prey:  2664
Intermediate-Predator:  1270
Predator:  1116
Empty:  4950
-----------------------------------------
Time Step:  24065
Prey:  2605
Intermediate-Predator:  1256
Predator:  1149
Empty:  4990
-----------------------------------------
Time Step:  24066
Prey:  2571
Intermediate-Predator:  1242
Predator:  1190
Empty:  4997
-----------------------------------------
Time Step:  24067
Prey:  2512
Intermediate-Predator:  1293
Predator:  1209
Empty:  4986
--

Intermediate-Predator:  1156
Predator:  1226
Empty:  5360
-----------------------------------------
Time Step:  24124
Prey:  2269
Intermediate-Predator:  1164
Predator:  1185
Empty:  5382
-----------------------------------------
Time Step:  24125
Prey:  2243
Intermediate-Predator:  1214
Predator:  1157
Empty:  5386
-----------------------------------------
Time Step:  24126
Prey:  2273
Intermediate-Predator:  1209
Predator:  1140
Empty:  5378
-----------------------------------------
Time Step:  24127
Prey:  2329
Intermediate-Predator:  1166
Predator:  1132
Empty:  5373
-----------------------------------------
Time Step:  24128
Prey:  2400
Intermediate-Predator:  1160
Predator:  1091
Empty:  5349
-----------------------------------------


SystemExit: 0